In [ ]:
# Let's import the necessary packages 
import os 
import numpy 

import cv2  # preprocessing I need this 
import warnings 
import numpy as np
import pandas as pd 
import matplotlib.pyplot as plt 
warnings.filterwarnings('ignore')

import tensorflow as tf 
from keras.models import Sequential 
from tensorflow.keras.layers import Dense,Flatten,Conv2D,MaxPooling2D, GlobalAveragePooling2D
from keras.preprocessing.image import ImageDataGenerator, load_img 

from IPython import display 
display.set_matplotlib_formats('svg')

In [ ]:
# Data loading 
train_gen = ImageDataGenerator(rescale = 1./255) # 0 to 255 pixels 

train_data = train_gen.flow_from_directory('../input/breedclassification/Breed Classification', target_size = (224, 224), 
                                          batch_size = 32, class_mode = 'categorical', shuffle = True)

In [ ]:
# Transfer learning 
from keras.applications.mobilenet_v2 import MobileNetV2,preprocess_input 

model = Sequential()
base_model = MobileNetV2(input_shape = [224, 224, 3], weights = 'imagenet', include_top = False)  

In [ ]:
# model correction 
base_model.trainable = True  

for i in base_model.layers[:100]: 
    base_model.trainable = False
    
pool = GlobalAveragePooling2D()
mid_layer = Dense(100,activation = 'relu')
final_1 = Dense(7,activation = 'softmax')

model = Sequential([base_model, mid_layer,pool, final_1])
model.summary()

In [ ]:
model.compile(loss = 'categorical_crossentropy',optimizer = 'adam',metrics = 'accuracy')
model.fit(train_data, epochs = 100)  # one variable (history)

In [ ]:
# Plot the accuracy! 
# plt.plot(history.history['acc'])
# plt.title('model accuracy')
# plt.ylabel('accuracy')
# plt.xlabel('epoch')
# plt.legend('train', loc='upper left')
# plt.show()

# # Plot the loss! 
# plt.plot(model.history['loss'])
# plt.title('model loss')
# plt.ylabel('loss')
# plt.xlabel('epoch')
# plt.legend('Loss', loc='upper left')
# plt.show()

In [ ]:
# Predict the new thing 
def predict_classes(link): 
    img = cv2.imread(link)
    img = cv2.resize(img,(224,224))
    img = img/255
    img = img.reshape(-1,224,224,3)    # -1 is  for reshaping basically 
    pred = np.round(model.predict(img)).argmax(axis = 1)
    dic = {0: 'Herding breed', 1: 'Hound breed', 2: 'Non sporting breed', 3: 'Terrior breed', 4:'working breed', 5: 'sporting breed', 6: 'toy breed'}
    print(dic.get(int(pred)))

In [ ]:
# predict 
link = './sample_image.png'
predict_classes(link)
print()
load_img(link)

In [ ]:
# classification report 
true_classes = train_data.classes
class_labels = list(train_data.class_indices.keys())

In [ ]:
from sklearn.metrics import classification_report,plot_confusion_matrix

y_hat = model.predict(train_data)
predicted_classes = np.argmax(y_hat, axis = 1)
report = classification_report(true_classes, predicted_classes, target_names = class_labels)
print(report)

In [ ]:
# saving the model 
model.save('breedclassification.h5')



In [ ]:
# to load the model 
# new_model = tf.keras.models.load_model('breedclassification.h5')
# new_model.predict(test_data) 

In [ ]:
import requests
response = requests.get("https://www.groomers-online.com/images/cms/sections/1598536220-35522500.png")

file = open("sample_image.png", "wb")
file.write(response.content)
file.close()

In [ ]:
# predict 
link = './sample_image.png'
predict_classes(link)
print()
load_img(link)

In [ ]:
# to load the model 
new_model = tf.keras.models.load_model('breedclassification.h5')


In [ ]:
# Predict the new thing 
def predict_classes(link): 
    img = cv2.imread(link)
    img = cv2.resize(img,(224,224))
    img = img/255
    img = img.reshape(-1,224,224,3)    # -1 is  for reshaping basically 
    pred = np.round(new_model.predict(img)).argmax(axis = 1)
    dic = {0: 'Herding breed', 1: 'Hound breed', 2: 'Non sporting breed', 3: 'Terrior breed', 4:'working breed', 5: 'sporting breed', 6: 'toy breed'}
    print(dic.get(int(pred)))

# predict 
link = './sample_image.png'
predict_classes(link)
print()
load_img(link)

In [ ]:
! pip install gradio 

In [ ]:
import gradio as gr
image = gr.inputs.Image(shape=(224, 224))
label = gr.outputs.Label(num_top_classes=7)

gr.Interface(fn=predict_classes, inputs=image, outputs=label,interpretation='default').launch() 